In [1]:
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings("ignore")
import seaborn as sns; sns.set()
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix,accuracy_score,recall_score,precision_score,f1_score
from sklearn.model_selection import train_test_split
from sklearn.decomposition import PCA
from sklearn.linear_model import LogisticRegression

from sklearn.preprocessing import StandardScaler


In [7]:
'''
print("Mounting your Google Drive ...")

from google.colab import drive
drive.flush_and_unmount()
drive.mount('/content/drive',force_remount=True)
 
path = "/content/drive/My Drive/clases-II-2021/Machine-Learning/datasets/taller03/"#Esta es la ruta
'''
path = 'C:/Users/Maria/Desktop/taller3/data'

In [8]:
biomedata_train_marker = 'biomedata_train_marker.csv'
biomedata_train_abundance = 'biomedata_train_abundance.csv'

biomedata_test_abundance = 'biomedata_test_abundance.csv'
biomedata_test_marker = 'biomedata_test_marker.csv'

In [11]:
data_train_marker = pd.read_csv(biomedata_train_marker,encoding='latin-1', index_col = 0)
data_train_abundance = pd.read_csv(biomedata_train_abundance,encoding='latin-1', index_col = 0)

data_test_marker = pd.read_csv(biomedata_test_marker,encoding='latin-1', index_col = 0)
data_test_abundance = pd.read_csv(biomedata_test_abundance,encoding='latin-1', index_col = 0)

In [129]:
data_train_abundance["Cirrhosis"].value_counts(dropna=False)

NaN    447
1.0     88
0.0     86
Name: Cirrhosis, dtype: int64

In [130]:
data_train_abundance["Diabetes"].value_counts(dropna=False)

NaN    363
0.0    130
1.0    128
Name: Diabetes, dtype: int64

In [131]:
data_train_abundance["Obesity"].value_counts(dropna=False)

NaN    432
1.0    123
0.0     66
Name: Obesity, dtype: int64

In [132]:
data_train_marker.shape

(621, 153953)

In [133]:
data_train_abundance.shape

(621, 717)

In [134]:
#data_train_abundance['Paciente'] = list(range(data_train_abundance.shape[0]))
#data_train_marker['Paciente'] = list(range(data_train_abundance.shape[0]))

In [135]:
#todo_train = pd.merge(data_train_abundance, data_train_marker, on=["Paciente"])
#todo_train.head()

In [136]:
#todo_test = pd.merge(biomedata_test_abundance, biomedata_test_marker, on=["Unnamed: 0"])
#todo_test.head() 

In [164]:
def join_data(enfermedad):
  data1 = data_train_abundance[data_train_abundance[enfermedad].notna()]
  data2 = data_train_marker[data_train_marker[enfermedad].notna()]
  data =  pd.concat([data1, data2], axis=1)
  return data.loc[:,~data.columns.duplicated()]

In [165]:
data_cirrosis = join_data("Cirrhosis")
print("Dimensiones de la Cirrosis: "+str(data_cirrosis.shape))
data_diabetes = join_data("Diabetes")
print("Dimensiones de la Diabetes: "+str(data_diabetes.shape))
data_obesidad = join_data("Obesity")
print("Dimensiones de la Obesidad: "+str(data_obesidad.shape))

Dimensiones de la Cirrosis: (174, 154663)
Dimensiones de la Diabetes: (258, 154663)
Dimensiones de la Obesidad: (189, 154663)


In [139]:
data_cirrosis.dropna(axis=1, how='all', inplace=True)
data_diabetes.dropna(axis=1, how='all', inplace=True)
data_obesidad.dropna(axis=1, how='all', inplace=True)

In [140]:
data_cirrosis.shape

(174, 121100)

In [141]:
def unico(df):
  drop=[]
  for column in df.columns:
    if len(df[column].unique())==1:
      drop.append(column)
  df=df.drop(drop,axis=1)
  return df


In [142]:
print('cirrosis',data_cirrosis.shape)
print('diabetes',data_diabetes.shape)
print('obesidad',data_obesidad.shape)

cirrosis (174, 121100)
diabetes (258, 120369)
obesidad (189, 100038)


In [143]:
data_cirrosis=unico(data_cirrosis)
data_diabetes=unico(data_diabetes)
data_obesidad=unico(data_obesidad)

In [144]:
print('cirrosis',data_cirrosis.shape)
print('diabetes',data_diabetes.shape)
print('obesidad',data_obesidad.shape)

cirrosis (174, 114966)
diabetes (258, 114412)
obesidad (189, 92308)


In [145]:
data_cirrosis.drop(['gender'],axis=1,inplace=True)
data_cirrosis.head()

Cirrhosis  \
0        1.0   
1        0.0   
2        0.0   
3        0.0   
4        1.0   

   k__Archaea|p__Euryarchaeota|c__Methanobacteria|o__Methanobacteriales|f__Methanobacteriaceae|g__Methanobrevibacter|s__Methanobrevibacter_smithii  \
0                                            0.02959                                                                                                 
1                                            0.00000                                                                                                 
2                                            0.00000                                                                                                 
3                                            0.29306                                                                                                 
4                                            0.00000                                                                                                 

   k__Archaea|p__Euryarchaeota|c__Methanobacteria|o__Methanobacteriales|f__Methanobacteriaceae|g__Methanobrevibacter|s__Methanobrevibacter_unclassified  \
0                                            0.00955                                                                                                      
1                                            0.00000                                                                                                      
2                                            0.00000                                                                                                      
3                                            0.00000                                                                                                      
4                                            0.00000                                                                                                      

   k__Archaea|p__Euryarchaeota|c__Methanobacteria|o__Methanobacteriales|f__Methanobacteriaceae|g__Methanosphaera|s__Methanosphaera_stadtmanae  \
0                                                0.0                                                                                            
1                                                0.0                                                                                            
2                                                0.0                                                                                            
3                                                0.0                                                                                            
4                                                0.0                                                                                            

   k__Archaea|p__Euryarchaeota|c__Methanococci|o__Methanococcales|f__Methanocaldococcaceae|g__Methanocaldococcaceae_unclassified  \
0                                                0.0                                                                               
1                                                0.0                                                                               
2                                                0.0                                                                               
3                                                0.0                                                                               
4                                                0.0                                                                               

   k__Bacteria|p__Acidobacteria|c__Acidobacteriia|o__Acidobacteriales|f__Acidobacteriaceae|g__Granulicella|s__Granulicella_unclassified  \
0                                                0.0                                                                                      
1                                                0.0                                                                                

In [146]:
data_diabetes.drop(['gender','code_study'],axis=1,inplace=True)
data_diabetes.head()

k__Archaea|p__Euryarchaeota|c__Methanobacteria|o__Methanobacteriales|f__Methanobacteriaceae|g__Methanobrevibacter|s__Methanobrevibacter_smithii  \
363                                                0.0                                                                                                 
364                                                0.0                                                                                                 
365                                                0.0                                                                                                 
366                                                0.0                                                                                                 
367                                                0.0                                                                                                 

     k__Archaea|p__Euryarchaeota|c__Methanobacteria|o__Methanobacteriales|f__Methanobacteriaceae|g__Methanobrevibacter|s__Methanobrevibacter_unclassified  \
363                                            0.00000                                                                                                      
364                                            0.00271                                                                                                      
365                                            0.00000                                                                                                      
366                                            0.00000                                                                                                      
367                                            0.00000                                                                                                      

     k__Archaea|p__Euryarchaeota|c__Methanobacteria|o__Methanobacteriales|f__Methanobacteriaceae|g__Methanosphaera|s__Methanosphaera_stadtmanae  \
363                                                0.0                                                                                            
364                                                0.0                                                                                            
365                                                0.0                                                                                            
366                                                0.0                                                                                            
367                                                0.0                                                                                            

     k__Archaea|p__Euryarchaeota|c__Methanococci|o__Methanococcales|f__Methanocaldococcaceae|g__Methanocaldococcaceae_unclassified  \
363                                                0.0                                                                               
364                                                0.0                                                                               
365                                                0.0                                                                               
366                                                0.0                                                                               
367                                                0.0                                                                               

     k__Bacteria|p__Acidobacteria|c__Acidobacteriia|o__Acidobacteriales|f__Acidobacteriaceae|g__Granulicella|s__Granulicella_unclassified  \
363                                                0.0                                                                                      
364                                                0.0                                                                                      
365                                   

In [147]:
#data_cirrosis = data_cirrosis.drop(['gender'],axis=1)
cirrhosis=list(data_cirrosis.columns)
cirrhosis.remove('Cirrhosis')

diabetes=list(data_diabetes.columns)
diabetes.remove('Diabetes')

obesidad=list(data_obesidad.columns)
obesidad.remove('Obesity')

In [148]:
X1=data_cirrosis[cirrhosis]
y1=data_cirrosis['Cirrhosis']

X_train1, X_test1, y_train1, y_test1 = train_test_split(X1, y1, test_size=0.2, random_state=0)
X_train1, X_val1, y_train1, y_val1 = train_test_split(X_train1, y_train1, test_size=0.2, random_state=0)



X2=data_diabetes[diabetes]
y2=data_diabetes['Diabetes']

X_train2, X_test2, y_train2, y_test2 = train_test_split(X2, y2, test_size=0.2, random_state=0)
X_train2, X_val2, y_train2, y_val2 = train_test_split(X_train2, y_train2, test_size=0.2, random_state=0)



X3=data_obesidad[obesidad]
y3=data_obesidad['Obesity']

X_train3, X_test3, y_train3, y_test3 = train_test_split(X3, y3, test_size=0.2, random_state=0)
X_train3, X_val3, y_train3, y_val3 = train_test_split(X_train3, y_train3, test_size=0.2, random_state=0)


In [149]:
scaler1 = StandardScaler()

non_categorical_asteriod=cirrhosis
scaler1.fit(X_train1[non_categorical_asteriod])

X_train = pd.DataFrame(scaler1.transform(X_train1[non_categorical_asteriod]),columns=non_categorical_asteriod)
X_val = pd.DataFrame(scaler1.transform(X_val1[non_categorical_asteriod]),columns=non_categorical_asteriod)
X_test = pd.DataFrame(scaler1.transform(X_test1[non_categorical_asteriod]),columns=non_categorical_asteriod)

In [150]:
scaler2 = StandardScaler()

non_categorical_asteriod=diabetes
scaler2.fit(X_train2[non_categorical_asteriod])

X_train2 = pd.DataFrame(scaler2.transform(X_train2[non_categorical_asteriod]),columns=non_categorical_asteriod)
X_val2 = pd.DataFrame(scaler2.transform(X_val2[non_categorical_asteriod]),columns=non_categorical_asteriod)
X_test2 = pd.DataFrame(scaler2.transform(X_test2[non_categorical_asteriod]),columns=non_categorical_asteriod)

In [151]:
scaler3 = StandardScaler()

non_categorical_asteriod=obesidad
scaler3.fit(X_train3[non_categorical_asteriod])

X_train3 = pd.DataFrame(scaler3.transform(X_train3[non_categorical_asteriod]),columns=non_categorical_asteriod)
X_val3 = pd.DataFrame(scaler3.transform(X_val3[non_categorical_asteriod]),columns=non_categorical_asteriod)
X_test3 = pd.DataFrame(scaler3.transform(X_test3[non_categorical_asteriod]),columns=non_categorical_asteriod)

## RELIEF

In [152]:
def update_weigh(random_sample, instance_intra_class, instance_inter_class, weighs, distances, m):
    for i in range( len(weighs) ):
        weighs[i] = weighs[i] - abs(instance_intra_class.values[0][i] - random_sample.values[0][i]) / (m*distances[0]) +  abs(instance_inter_class.values[0][i] - random_sample.values[0][i])/(m*distances[1]) 

###  1.- Cirrosis

In [153]:
from scipy.spatial.distance import pdist, squareform


distances = pdist(X_train, metric='euclidean')

dist_matrix = squareform(distances)

m = 200 # interation number

feature_weighs = np.zeros( len(cirrhosis) )

# RELIEF ALGORITHM, expropiado de la ayudantia 6

for i in range(m):

    random_number = np.random.randint(X_train.shape[0])
    random_sample = X_train.iloc[[  random_number ]]
    #print("\nrandom_sample: \n")
    #print(random_sample)

    random_sample_category = y_train.iloc[[  random_number ]].values
    
    #print("random sample category :", random_sample_category)


    distances = [np.Inf, np.Inf] # intra, inter

    instance_intra_class =  X_train.iloc[[ 0 ]]
    instance_inter_class = X_train.iloc[[ 0 ]]
    
    for i, distance in enumerate(dist_matrix[random_number]): # seleccionar la fila respectiva en la matriz de distancias
    
        if ( y_train.iloc[[  i ]].values[0] == random_sample_category): # distancia intra class 
            if (distance <  distances[0]):
                if (i == random_number):
                    continue
                distances[0] = distance
                instance_intra_class =  X_train.iloc[[ i ]].copy()
        
        else: # distancia inter class 
            if (distance < distances[1]):
                if (i == random_number):
                    continue
                distances[1] = distance
                instance_inter_class = X_train.iloc[[ i ]].copy()

    #print("(min distance intra class, min distance inter class): ", (distances[0], distances[1]))

    update_weigh(random_sample, instance_intra_class, instance_inter_class, feature_weighs, distances, m)


#print("feature_weighs: ")
#print(feature_weighs)

k = int(X_train.shape[1]*0.3)
#k = 5

idx = np.argpartition(feature_weighs, -k)[-k:]
indices = idx[np.argsort((-feature_weighs)[idx])]

#print("indices: ", indices)

#print()

print("top features cirrosis: ")

top_features1 = []
for i in indices:
    top_features1.append( cirrhosis[i] )
    print(cirrhosis[i])

# en el top se encuentra e (excentricidad) y per (perihelio).  Ambos correlacionados. 

top features cirrosis: 
gi|218292277|ref|NZ_ACCK01000024.1|:64981-65625
gi|545349566|ref|NZ_KE952233.1|:1-158
gi|282877883|ref|NZ_ADEG01000045.1|:26519-27439
gi|256402719|ref|NZ_GG698602.1|:1300899-1301624
gi|545616023|ref|NZ_KI271163.1|:c6669-5347
gi|423314206|ref|NZ_JH724285.1|:193527-195143
gi|483522911|ref|NZ_AMQA01000004.1|:261682-262251
gi|420152916|ref|NZ_AKFT01000102.1|:5410-5961
gi|282878133|ref|NZ_ADEG01000057.1|:c11344-10823
gi|420152841|ref|NZ_AKFT01000098.1|:31693-32274
gi|512218208|dbj|BAOU01000046.1|:c6021-5893
gi|224514987|ref|NZ_DS499697.1|:c176565-176086
gi|419955909|ref|NZ_AJXE01000029.1|:c1260-793
gi|423314206|ref|NZ_JH724285.1|:193281-193511
gi|228469918|ref|NZ_ACLR01000089.1|:c813-181
gi|545329273|ref|NZ_KE951477.1|:22940-23515
gi|399517736|ref|NZ_CAKV01000100.1|:c1370-651
gi|283767235|ref|NZ_GG730309.1|:c473736-473479
gi|134301158|ref|NZ_AAVM02000001.1|:c867342-867139
gi|253584468|ref|NZ_GG694029.1|:c200007-199420
gi|479336697|ref|NC_021047.1|:2086899-2087516
gi|

gi|336434658|ref|NZ_GL945339.1|:c198863-197787
gi|294794157|ref|NZ_GG770200.1|:377233-377649
gi|224485443|ref|NZ_EQ973178.1|:285294-285590
gi|379704392|ref|NC_016826.1|:c1745497-1745339
gi|313893748|ref|NZ_AENU01000018.1|:c48575-48252
gi|224514723|ref|NZ_DS480679.1|:c12676-12125
gi|322372294|ref|NZ_GL698449.1|:91498-92180
gi|492714479|ref|NZ_KB905467.1|:724617-725522
gi|224581027|ref|NZ_GG657552.1|:185357-185581
gi|226597590|ref|NZ_GG663524.1|:c833662-833117
gi|313892865|ref|NZ_AENU01000007.1|:c139896-139594
gi|379704392|ref|NC_016826.1|:225307-225537
gi|423242654|ref|NZ_JH724166.1|:c4104-3769
gi|345651617|ref|NZ_JH114360.1|:28845-29984
gi|313894141|ref|NZ_AENU01000019.1|:c73537-72905
gi|322373756|ref|NZ_GL698450.1|:60838-61710
gi|552737301|ref|NC_022584.1|:363737-364378
gi|556489051|ref|NZ_KI535658.1|:653579-653713
gi|379704392|ref|NC_016826.1|:281071-281541
gi|110798562|ref|NC_008261.1|:c1853240-1852644
gi|423278997|ref|NZ_JH815483.1|:c507264-506239
gi|479152295|ref|NC_021014.1|:2854

gi|134301158|ref|NZ_AAVM02000001.1|:c874996-874817
gi|257789778|ref|NC_013204.1|:810699-812090
gi|419800290|ref|NZ_AJMV01000089.1|:c10683-9988
gi|223045081|ref|NZ_ACEP01000033.1|:c7573-6413
gi|423311451|ref|NZ_JH724282.1|:c25921-25802
gi|237640064|ref|NZ_GG667605.1|:326376-327056
gi|423332908|ref|NZ_JH976496.1|:c1378282-1377035
gi|346681619|ref|NZ_JH126487.1|:c187256-185595
gi|512697125|ref|NZ_KE150483.1|:c1125360-1125046
gi|410105719|ref|NZ_JH976501.1|:c641182-640703
gi|313893564|ref|NZ_AENU01000015.1|:c29571-29125
gi|410105720|ref|NZ_JH976502.1|:c351922-349829
gi|492707081|ref|NZ_KB905466.1|:c213520-213386
gi|401680137|ref|NZ_ALKL01000011.1|:c16662-7537
gi|479155735|ref|NC_021015.1|:3298016-3300466
gi|512436219|ref|NZ_KE159507.1|:220080-221105
gi|484029956|ref|NZ_HE978648.1|:1355667-1355903
gi|397320020|ref|NZ_JH724309.1|:325983-327128
gi|423332908|ref|NZ_JH976496.1|:911275-912822
gi|401679713|ref|NZ_ALKL01000010.1|:58465-58785
gi|224993744|ref|NZ_ACFY01000053.1|:c15292-14273
gi|2983

gi|336412492|ref|NZ_GL945043.1|:1913590-1914855
gi|262380949|ref|NZ_GG705149.1|:c1489158-1487641
gi|550766529|ref|NZ_AXLJ01000001.1|:3365725-3366570
gi|225594904|ref|NZ_GG662012.1|:169683-170873
gi|397320020|ref|NZ_JH724309.1|:52446-53741
gi|357048618|ref|NZ_JH376597.1|:438123-438245
gi|423313760|ref|NZ_JH724284.1|:211145-214651
gi|283767237|ref|NZ_GG730311.1|:c121474-120434
gi|384096982|ref|NZ_JH636037.1|:c939909-938989
gi|556295823|ref|NZ_KI535451.1|:1709833-1710747
gi|545392599|ref|NZ_KE992571.1|:c1300-770
gi|355687109|ref|NZ_JH376421.1|:c482426-481446
gi|265762432|ref|NZ_GG705209.1|:641500-642030
gi|479136967|ref|NC_021009.1|:2720302-2721189
gi|346681182|ref|NZ_JH126433.1|:532109-532687
gi|336434663|ref|NZ_GL945344.1|:c58892-58434
gi|223045181|ref|NZ_ACEP01000131.1|:5290-5502
gi|384096969|ref|NZ_JH636044.1|:1521846-1523369
gi|224515087|ref|NZ_DS995348.1|:c390334-389345
gi|397320021|ref|NZ_JH724310.1|:187712-188596
gi|512436190|ref|NZ_KE159478.1|:162880-163608
gi|492707081|ref|NZ_KB

gi|479201824|ref|NC_021040.1|:1841331-1841858
gi|423274991|ref|NZ_JH724195.1|:411968-413095
gi|330998632|ref|NZ_GL883867.1|:c8845-5930
gi|405321593|ref|NZ_JH815203.1|:630322-633216
gi|329958415|ref|NZ_GL882583.1|:371640-371792
gi|397320018|ref|NZ_JH724307.1|:c740239-739223
gi|405322024|ref|NZ_JH815204.1|:c601595-601011
gi|225594899|ref|NZ_GG662007.1|:13245-13988
gi|329958303|ref|NZ_GL882581.1|:c75186-74731
gi|225001188|ref|NZ_DS990179.1|:64276-64917
gi|384096967|ref|NZ_JH636027.1|:82912-83991
gi|423280955|ref|NZ_JH815485.1|:522585-523211
gi|488647692|ref|NZ_KB851023.1|:c1063168-1062443
gi|419856151|ref|NZ_AJTM01000062.1|:105992-106309
gi|329958415|ref|NZ_GL882583.1|:c389600-389460
gi|375087559|ref|NZ_JH601090.1|:169050-169631
gi|330021992|ref|NZ_GL882786.1|:c30378-30154
gi|211596835|ref|NZ_DS264289.1|:8815-9255
gi|329958515|ref|NZ_GL882584.1|:139086-139232
gi|564726352|gb|AZJE01000001.1|:19183-19443
gi|330998652|ref|NZ_GL883887.1|:c80347-79733
gi|313897937|ref|NZ_AENW01000006.1|:c25991

...

gi|512535830|ref|NZ_KE150441.1|:1544292-1545455
gi|418035027|ref|NZ_AGHW01000008.1|:13878-14531
gi|257789778|ref|NC_013204.1|:338125-339165
gi|222444358|ref|NZ_ABXX02000006.1|:112020-112223
gi|313893446|ref|NZ_AENU01000014.1|:c10360-8591
gi|459825443|ref|NZ_AOTD01000010.1|:5646-6169
gi|483523457|ref|NZ_AMQA01000012.1|:15584-16207
gi|410591375|ref|NZ_BAFL01000001.1|:c754414-753626
gi|340354300|ref|NZ_GL982514.1|:c650343-649510
gi|422323853|ref|NZ_JH370351.1|:794889-795344
gi|422330174|ref|NZ_JH590973.1|:16773-16982
gi|479176048|ref|NC_021022.1|:3356948-3358006
gi|410101291|ref|NZ_JH976477.1|:c311930-310707
gi|551720208|ref|NZ_KI391970.1|:c336920-336432
gi|422344460|ref|NZ_JH376860.1|:c48390-47950
gi|170764318|ref|NZ_ABIX02000002.1|:2554243-2554536
gi|346681182|ref|NZ_JH126433.1|:601329-604046
gi|420147584|ref|NZ_AKFQ01000002.1|:72542-72844
gi|377831605|ref|NZ_AHIT01000023.1|:c54458-53628
gi|348025247|ref|NC_015873.1|:1497867-1498550
gi|257461344|ref|NZ_ACYG01000032.1|:c82650-81943
gi|22

gi|538346599|ref|NC_022236.1|:c1815469-1813064
gi|484006680|ref|NZ_KB894545.1|:249240-249794
gi|283457089|ref|NC_013715.1|:c1780205-1779090
gi|479324019|ref|NC_021057.1|:c223960-223484
gi|358468230|ref|NZ_JH378933.1|:c1153-617
gi|479146200|ref|NC_021012.1|:c2500695-2500072
gi|507091347|ref|NZ_KB976100.1|:c4491015-4490848
gi|420148019|ref|NZ_AKFQ01000004.1|:14812-15387
gi|523687972|ref|NZ_ASRG01000005.1|:c21566-20070
gi|313150996|ref|NZ_GL379580.1|:c641199-640789
gi|523687695|ref|NZ_ASRG01000002.1|:c42108-41107
gi|253584466|ref|NZ_GG694027.1|:c402647-401808
gi|410591404|ref|NZ_BAFL01000030.1|:c109955-109368
gi|483984517|ref|NZ_KB892637.1|:c240554-239841
gi|184154476|ref|NC_010610.1|:427592-428677
gi|253584454|ref|NZ_GG694015.1|:c585652-584381
gi|448879147|ref|NZ_KB373314.1|:c1088376-1085066
gi|322378310|ref|NZ_GL732507.1|:c599-48
gi|331640194|ref|NZ_GL890551.1|:c203128-202067
gi|298386634|ref|NZ_GG774708.1|:438353-439105
gi|385263145|ref|NZ_AJMM01000031.1|:92731-93198
gi|238694502|ref|N

gi|397320019|ref|NZ_JH724308.1|:667786-669300
gi|340536304|ref|NZ_GL985618.1|:c295160-294870
gi|260590259|ref|NZ_ACEO02000010.1|:6457-6576
gi|422323853|ref|NZ_JH370351.1|:c644907-644695
gi|488679034|ref|NZ_KB850943.1|:c2063047-2062472
gi|365829568|ref|NZ_JH470349.1|:c186238-185837
k__Bacteria|p__Proteobacteria|c__Gammaproteobacteria|o__Enterobacteriales|f__Enterobacteriaceae|g__Klebsiella|s__Klebsiella_oxytoca
gi|512633855|ref|NZ_KE150451.1|:c573692-571842
gi|282856345|ref|NZ_ADFP01000051.1|:c36988-36563
gi|402311893|ref|NZ_ALJL01000016.1|:c8474-7635
gi|309778561|ref|NZ_GL520134.1|:c394261-393530
gi|242366431|ref|NZ_GG693221.1|:250105-250359
gi|312868614|ref|NZ_AEKL01000005.1|:22523-23371
gi|301299977|ref|NZ_AEBA01000066.1|:16330-16803
gi|224514940|ref|NZ_DS499651.1|:490-639
gi|257124814|ref|NC_013192.1|:c46703-45984
gi|423111342|ref|NZ_JH603144.1|:656589-657149
gi|390630485|ref|NZ_CAGH01000016.1|:c36157-35957
gi|365137247|ref|NZ_JH414706.1|:c1124162-1122489
gi|551717783|ref|NZ_KI39197

gi|405795786|ref|NZ_JH815221.1|:87882-88202
gi|405795787|ref|NZ_JH815222.1|:c2466894-2464000
gi|488650489|ref|NC_021175.1|:c1301823-1301380
gi|405795787|ref|NZ_JH815222.1|:c1734660-1734142
gi|405795787|ref|NZ_JH815222.1|:c1624961-1623909
gi|405795787|ref|NZ_JH815222.1|:c3185021-3184782
gi|405795785|ref|NZ_JH815220.1|:c46109-44793
gi|257459355|ref|NZ_ACYG01000017.1|:c23706-23509
gi|302380481|ref|NZ_AECM01000025.1|:253445-254380
gi|405795787|ref|NZ_JH815222.1|:804087-804770
gi|405795787|ref|NZ_JH815222.1|:219930-220373
gi|405795787|ref|NZ_JH815222.1|:1470504-1471082
gi|405795787|ref|NZ_JH815222.1|:c2152616-2151315
gi|405795787|ref|NZ_JH815222.1|:c1835907-1835275
gi|405795787|ref|NZ_JH815222.1|:1981115-1981459
gi|405795787|ref|NZ_JH815222.1|:170244-170711
gi|405795787|ref|NZ_JH815222.1|:1529177-1529752
gi|324996374|ref|NZ_BABV01000059.1|:6272-7108
gi|545615639|ref|NZ_KI271151.1|:c38301-38128
gi|325854944|ref|NZ_AEXO01000032.1|:8311-8802
gi|448879147|ref|NZ_KB373314.1|:56080-56751
gi|50167

gi|239633765|ref|NZ_GG670287.1|:437954-438178
gi|239633764|ref|NZ_GG670286.1|:c685917-685684
gi|239633765|ref|NZ_GG670287.1|:347190-347357
gi|239633765|ref|NZ_GG670287.1|:c350083-349748
gi|239633765|ref|NZ_GG670287.1|:c360680-360345
gi|239633764|ref|NZ_GG670286.1|:c216620-216084
gi|239633770|ref|NZ_GG670292.1|:83888-84460
gi|239633764|ref|NZ_GG670286.1|:c446224-446015
gi|239633764|ref|NZ_GG670286.1|:539760-540692
gi|239633768|ref|NZ_GG670290.1|:c134863-134687
gi|257124814|ref|NC_013192.1|:c732979-731519
gi|448879147|ref|NZ_KB373314.1|:c360684-360250
k__Bacteria|p__Firmicutes|c__Erysipelotrichia|o__Erysipelotrichales|f__Erysipelotrichaceae|g__Erysipelotrichaceae_noname|s__Erysipelotrichaceae_bacterium_21_3
gi|224485392|ref|NZ_EQ973127.1|:c84372-84259
gi|322376215|ref|NZ_GL732486.1|:c583315-583013
gi|319430588|ref|NZ_GL622611.1|:100310-100669
gi|241888914|ref|NZ_ACDZ02000008.1|:73664-74431
gi|222444355|ref|NZ_ABXX02000003.1|:465852-467552
gi|479179495|ref|NC_021023.1|:c645732-645202
gi|3

### 2.- Diabetes

In [154]:
from scipy.spatial.distance import pdist, squareform


distances = pdist(X_train2, metric='euclidean')

dist_matrix = squareform(distances)

m = 200 # interation number

feature_weighs2 = np.zeros( len(diabetes) )

# RELIEF ALGORITHM, expropiado de la ayudantia 6

for i in range(m):

    random_number = np.random.randint(X_train2.shape[0])
    random_sample = X_train2.iloc[[  random_number ]]
    #print("\nrandom_sample: \n")
    #print(random_sample)

    random_sample_category = y_train2.iloc[[  random_number ]].values
    
    #print("random sample category :", random_sample_category)


    distances = [np.Inf, np.Inf] # intra, inter

    instance_intra_class =  X_train2.iloc[[ 0 ]]
    instance_inter_class = X_train2.iloc[[ 0 ]]
    
    for i, distance in enumerate(dist_matrix[random_number]): # seleccionar la fila respectiva en la matriz de distancias
    
        if ( y_train2.iloc[[  i ]].values[0] == random_sample_category): # distancia intra class 
            if (distance <  distances[0]):
                if (i == random_number):
                    continue
                distances[0] = distance
                instance_intra_class =  X_train2.iloc[[ i ]].copy()
        
        else: # distancia inter class 
            if (distance < distances[1]):
                if (i == random_number):
                    continue
                distances[1] = distance
                instance_inter_class = X_train2.iloc[[ i ]].copy()

    #print("(min distance intra class, min distance inter class): ", (distances[0], distances[1]))

    update_weigh(random_sample, instance_intra_class, instance_inter_class, feature_weighs2, distances, m)


#print("feature_weighs2: ")
#print(feature_weighs2)

k = int(X_train2.shape[1]*0.3)
#k = 5

idx = np.argpartition(feature_weighs2, -k)[-k:]
indices = idx[np.argsort((-feature_weighs2)[idx])]

#print("indices: ", indices)

#print()
print("top features2: ")

top_features2 = []
for i in indices:
    top_features2.append(diabetes[i])
    print(diabetes[i])

# en el top se encuentra e (excentricidad) y per (perihelio).  Ambos correlacionados. 

top features2: 
gi|340792956|ref|NC_015859.1|:c1041819-1041136
gi|425062680|ref|NZ_CM001580.1|:1910088-1910444
gi|397668839|ref|NC_018142.1|:2053863-2054327
gi|397668839|ref|NC_018142.1|:2404568-2404771
gi|423278997|ref|NZ_JH815483.1|:c512049-511819
gi|406351917|ref|NZ_JH815232.1|:642305-642637
gi|423280955|ref|NZ_JH815485.1|:187646-187738
gi|242362087|ref|NZ_GG692725.1|:c103552-103328
gi|507383177|ref|NC_021284.1|:164654-165889
gi|510837049|ref|NZ_ASRV01000202.1|:c2774-1986
gi|512535830|ref|NZ_KE150441.1|:c1537866-1537666
gi|483966906|ref|NZ_CAEJ01000127.1|:c310266-309946
gi|319430416|ref|NZ_GL622579.1|:c258380-257906
gi|184199646|ref|NC_010617.1|:c251782-250982
gi|343522960|ref|NZ_AFUR01000002.1|:c108994-108806
gi|551720532|ref|NZ_KI391958.1|:c43997-42867
gi|339639717|ref|NZ_AFQU01000001.1|:c184292-183849
gi|551720568|ref|NZ_KI391960.1|:20303-20983
gi|512536257|ref|NZ_KE150442.1|:c128418-127573
gi|405795787|ref|NZ_JH815222.1|:263521-263685
gi|479199283|ref|NC_021039.1|:c1905827-19054

gi|479152295|ref|NC_021014.1|:1455239-1456381
gi|512436177|ref|NZ_KE159465.1|:c794881-794322
gi|424661815|ref|NZ_JH815524.1|:c1136713-1134656
gi|417937259|ref|NZ_AFUQ01000015.1|:c59430-59068
gi|225618950|ref|NC_012225.1|:2265511-2266164
gi|483364578|ref|NZ_KB903359.1|:478018-478923
gi|355686923|ref|NZ_JH376420.1|:c1237685-1236783
gi|223045052|ref|NZ_ACEP01000004.1|:c23904-23734
gi|224021168|ref|NZ_DS544177.1|:141380-142132
gi|323142631|ref|NZ_GL830888.1|:54083-54526
gi|299144573|ref|NZ_GG774949.1|:c1728066-1727748
gi|224021172|ref|NZ_DS544181.1|:38033-38431
gi|545413440|ref|NZ_KE993401.1|:30591-30881
gi|355632463|ref|NZ_JH376517.1|:c273396-273007
gi|324035750|ref|NZ_GL834309.1|:281969-282100
gi|346681182|ref|NZ_JH126433.1|:297818-298210
gi|301311308|ref|NZ_GG774999.1|:c323681-323082
gi|390945347|ref|NC_018011.1|:1652138-1652569
gi|225594899|ref|NZ_GG662007.1|:c314159-313590
gi|512690811|ref|NZ_KE150480.1|:636043-637542
gi|224486047|ref|NZ_GG657595.1|:c368670-367489
gi|488641608|ref|NZ_

gi|211596884|ref|NZ_DS264338.1|:68614-68988
gi|423307260|ref|NZ_JH724268.1|:c1917547-1917173
gi|514340171|ref|NZ_KE150406.1|:1053095-1053937
gi|484029956|ref|NZ_HE978648.1|:857940-858263
gi|484006757|ref|NZ_KB894553.1|:75570-76895
gi|482747434|ref|NZ_HE998568.1|:c826579-825713
gi|223045112|ref|NZ_ACEP01000064.1|:104690-105712
gi|479176048|ref|NC_021022.1|:3505497-3506240
gi|482849893|ref|NZ_AKBX01000001.1|:c1171357-1170563
gi|384096983|ref|NZ_JH636038.1|:96044-96313
gi|545443428|ref|NZ_KI260299.1|:c1244-945
gi|479170689|ref|NC_021020.1|:c2875215-2875033
gi|223045135|ref|NZ_ACEP01000085.1|:7119-7409
gi|479136967|ref|NC_021009.1|:2698870-2699076
gi|119025018|ref|NC_008618.1|:2073409-2074041
gi|512436175|ref|NZ_KE159463.1|:49270-50172
gi|365124760|ref|NZ_JH414775.1|:c19172-18216
gi|385261250|ref|NZ_AJML01000040.1|:46245-46733
gi|423344639|ref|NZ_JH976452.1|:c985649-984825
gi|479143419|ref|NC_021011.1|:c674727-674467
gi|325838175|ref|NZ_AEXQ01000014.1|:8250-9194
gi|225594900|ref|NZ_GG66200

gi|479146200|ref|NC_021012.1|:1671652-1671930
gi|298374875|ref|NZ_GG774760.1|:c637595-637212
gi|384096986|ref|NZ_JH636041.1|:c222101-222003
gi|424661815|ref|NZ_JH815524.1|:c2548886-2548272
gi|484029948|ref|NZ_HE978647.1|:c493181-492030
gi|211596884|ref|NZ_DS264338.1|:c64051-63599
gi|479140210|ref|NC_021010.1|:651310-651441
gi|134302808|ref|NZ_AAVM02000016.1|:c10627-10472
gi|242353471|ref|NZ_GG688317.1|:c537648-536677
gi|354605451|ref|NZ_JH370371.1|:c699702-699040
gi|479150083|ref|NC_021013.1|:c497860-497147
gi|146386232|ref|NZ_AAYG02000016.1|:158399-159868
gi|375087559|ref|NZ_JH601090.1|:310610-312106
gi|375087559|ref|NZ_JH601090.1|:c310319-308517
gi|375087559|ref|NZ_JH601090.1|:c328975-325976
gi|375087559|ref|NZ_JH601090.1|:c321061-318599
gi|375087559|ref|NZ_JH601090.1|:c330289-328988
gi|375087559|ref|NZ_JH601090.1|:c305802-304036
gi|485040770|ref|NZ_AELY01000018.1|:c87964-87338
gi|448879147|ref|NZ_KB373314.1|:c354415-352679
gi|452215691|ref|NZ_AEJU01000186.1|:56545-56922
gi|242366475

gi|479143419|ref|NC_021011.1|:c683682-683548
gi|224021127|ref|NZ_DS499577.1|:c976588-976358
gi|119025018|ref|NC_008618.1|:605287-606042
gi|545627795|ref|NZ_KI271530.1|:46078-46500
gi|479150083|ref|NC_021013.1|:582378-583535
gi|423291533|ref|NZ_JH724230.1|:233889-235124
gi|423291533|ref|NZ_JH724230.1|:236820-239009
gi|298479577|ref|NZ_GG774795.1|:c338034-336787
gi|224514716|ref|NZ_DS480674.1|:c23104-22424
gi|256840174|ref|NZ_GG698740.1|:c614069-612048
gi|423221344|ref|NZ_JH724085.1|:c1060764-1060270
gi|545390724|ref|NZ_KE992388.1|:c42984-42394
gi|270293478|ref|NZ_GG730105.1|:263872-267027
gi|270293478|ref|NZ_GG730105.1|:275807-276568
gi|270293478|ref|NZ_GG730105.1|:257852-258856
gi|270293478|ref|NZ_GG730105.1|:274385-275398
gi|270293478|ref|NZ_GG730105.1|:272152-274380
gi|270293478|ref|NZ_GG730105.1|:271458-271922
gi|512697125|ref|NZ_KE150483.1|:1477254-1477658
gi|390945347|ref|NC_018011.1|:921085-921771
gi|298377884|ref|NZ_GG774768.1|:c7259-6006
gi|384096974|ref|NZ_JH636029.1|:c1035147

...

gi|354605452|ref|NZ_JH370372.1|:258985-260316
gi|307244576|ref|NZ_ADGQ01000071.1|:54020-54769
gi|242362087|ref|NZ_GG692725.1|:c118235-117822
gi|479146200|ref|NC_021012.1|:2005664-2006377
gi|489118444|ref|NZ_AOUE01000016.1|:c278878-278423
gi|346306065|ref|NZ_JH114238.1|:21736-24081
gi|552628837|ref|NC_022582.1|:c882645-882115
gi|251833058|ref|NZ_GG693415.1|:278207-278689
gi|146386181|ref|NZ_AAXG02000032.1|:75143-75349
gi|313897169|ref|NZ_AENW01000002.1|:c54944-54795
gi|423286106|ref|NZ_JH724226.1|:2350356-2351138
gi|307719921|ref|NC_014506.1|:221678-221896
gi|401681725|ref|NZ_ALKI01000011.1|:c74426-74031
gi|510805587|ref|NZ_KE136363.1|:c266969-266697
gi|374534871|ref|NZ_AEEA01000019.1|:c27038-26493
gi|514979630|ref|NZ_KE340299.1|:c214890-214126
gi|254692778|ref|NZ_GG697156.2|:89915-90184
gi|257441020|ref|NZ_GG700527.1|:253602-253889
gi|346306065|ref|NZ_JH114238.1|:37157-39013
gi|414353738|ref|NZ_DS995342.4|:147237-147359
gi|374627926|ref|NZ_JH599901.1|:121520-121618
gi|419838566|ref|NZ_

gi|224485791|ref|NZ_EQ973643.1|:c497261-496278
gi|224485783|ref|NZ_EQ973635.1|:153240-153431
gi|224485780|ref|NZ_EQ973632.1|:147955-149304
gi|224485792|ref|NZ_EQ973644.1|:c37422-36523
gi|224485791|ref|NZ_EQ973643.1|:c498515-497331
gi|224581370|ref|NZ_GG658170.1|:2109027-2109446
gi|410101289|ref|NZ_JH976475.1|:457336-458187
gi|284047386|ref|NC_013740.1|:647974-648297
gi|557594262|gb|AYHA01000068.1|:6951-7886
gi|452217962|ref|NZ_AEJY01000346.1|:4233-4653
gi|241888914|ref|NZ_ACDZ02000008.1|:143930-144718
gi|479150083|ref|NC_021013.1|:1862764-1863075
gi|211596831|ref|NZ_DS264285.1|:c29818-27440
gi|363895787|ref|NZ_JH414547.1|:c3559-2969
gi|284047386|ref|NC_013740.1|:456898-457362
gi|410105718|ref|NZ_JH976500.1|:140458-143706
gi|224485444|ref|NZ_EQ973179.1|:c245148-241900
gi|429086176|ref|NZ_CAKX01000221.1|:c337239-336772
gi|319430547|ref|NZ_GL622501.1|:c81893-80967
gi|422330174|ref|NZ_JH590973.1|:20426-21784
gi|545420410|ref|NZ_KE993553.1|:c128225-127377
gi|510932120|ref|NZ_KE136510.1|:c15

gi|422843625|ref|NZ_GL872382.1|:c20154-19498
gi|423311451|ref|NZ_JH724282.1|:c1485272-1483143
gi|479173639|ref|NC_021021.1|:c3107913-3107545
gi|485075851|ref|NZ_KB906628.1|:17149-18333
gi|384096968|ref|NZ_JH636043.1|:c17202-16090
gi|397320018|ref|NZ_JH724307.1|:2739622-2740647
gi|223667806|ref|NZ_DS480317.1|:c122500-121976
gi|365823354|ref|NC_014624.2|:433025-433372
gi|522835080|ref|NZ_KE350266.1|:212105-212473
gi|239633765|ref|NZ_GG670287.1|:430438-430602
gi|239633768|ref|NZ_GG670290.1|:c134863-134687
gi|239633764|ref|NZ_GG670286.1|:663616-663894
gi|484227745|ref|NZ_AQWR01000032.1|:c3368-2754
gi|284047386|ref|NC_013740.1|:c1334389-1333148
gi|284047386|ref|NC_013740.1|:225951-226220
gi|284047386|ref|NC_013740.1|:c425078-424518
gi|284047386|ref|NC_013740.1|:1049832-1050263
gi|406584897|ref|NZ_AJQZ01000044.1|:c84462-84298
gi|410938114|ref|NZ_AJRF02000018.1|:c12324-12157
gi|522836821|ref|NZ_KE352447.1|:215614-215967
gi|410936685|ref|NZ_AJRF02000012.1|:c185976-185854
gi|451952339|ref|NZ_AJ

gi|260447107|ref|NZ_GG703879.1|:1254382-1255065
gi|427395956|ref|NZ_JH992914.1|:c503590-503297
gi|410936685|ref|NZ_AJRF02000012.1|:c179091-178816
gi|406591107|ref|NZ_AJQX01000151.1|:27301-28131
gi|469923890|ref|NZ_KB029547.1|:c448377-447793
gi|410936685|ref|NZ_AJRF02000012.1|:c131124-130222
gi|422325652|ref|NZ_JH590968.1|:102671-102826
gi|224515008|ref|NZ_DS499711.1|:c64143-63664
gi|225594889|ref|NZ_GG661997.1|:c232871-232305
gi|225594886|ref|NZ_GG661994.1|:479640-480002
gi|300814831|ref|NZ_AEAA01000138.1|:c25271-24351
gi|484028026|ref|NZ_HE978532.1|:c108090-107470
gi|282882995|ref|NZ_ADDO01000060.1|:c18903-18673
gi|320528834|ref|NZ_GL637654.1|:c32377-31793
gi|300813732|ref|NZ_AEAA01000054.1|:c4196-3945
gi|553312887|ref|NZ_AWXC01000034.1|:c15668-12972
gi|484088171|ref|NZ_KB900371.1|:c99824-99348
gi|484028026|ref|NZ_HE978532.1|:c107443-106487
gi|282881978|ref|NZ_ADDO01000021.1|:c137570-137022
gi|282876978|ref|NZ_ADEG01000008.1|:c2805-595
gi|282882449|ref|NZ_ADDO01000041.1|:14988-15758
g

gi|282859866|ref|NZ_ADFO01000101.1|:82271-83236
gi|282856265|ref|NZ_ADFP01000048.1|:c1733-1572
gi|544227641|gb|AWVI01000121.1|:c8313-8032
gi|391311639|gb|AKNF01000993.1|:c9159-7561
gi|290512895|ref|NZ_GG745515.1|:97074-98066
gi|479173639|ref|NC_021021.1|:1716291-1716884
gi|484030447|ref|NZ_HE978651.1|:129695-130153
gi|484229072|ref|NZ_AKCB01000001.1|:2185325-2185420
gi|149172908|ref|NZ_ABBX01000006.1|:c8562-8332
gi|479150083|ref|NC_021013.1|:c1293991-1293518
gi|224021189|ref|NZ_DS560018.1|:c157435-156896
gi|421843377|ref|NZ_ANAV01000001.1|:290984-291505
gi|15671982|ref|NC_002662.1|:c2038137-2037253
gi|283769455|ref|NZ_ADFR01000016.1|:c130348-130166
gi|313888083|ref|NZ_AENP01000012.1|:c91703-91227
gi|410101288|ref|NZ_JH976474.1|:890913-892370
gi|335049439|ref|NZ_AFIJ01000026.1|:c33282-32068
gi|553308997|ref|NZ_AWXA01000041.1|:84415-85374
gi|312899187|ref|NZ_GL538209.1|:24571-26073
gi|312899153|ref|NZ_GL538175.1|:22936-24237
gi|320099583|ref|NZ_GL636615.1|:928157-929338
gi|512220106|dbj|

### 3.- Obesidad

In [155]:
from scipy.spatial.distance import pdist, squareform


distances = pdist(X_train3, metric='euclidean')

dist_matrix = squareform(distances)

m = 200 # interation number

feature_weighs3 = np.zeros( len(obesidad) )

# RELIEF ALGORITHM, expropiado de la ayudantia 6

for i in range(m):

    random_number = np.random.randint(X_train3.shape[0])
    random_sample = X_train3.iloc[[  random_number ]]
    #print("\nrandom_sample: \n")
    #print(random_sample)

    random_sample_category = y_train3.iloc[[  random_number ]].values
    
    #print("random sample category :", random_sample_category)


    distances = [np.Inf, np.Inf] # intra, inter

    instance_intra_class =  X_train3.iloc[[ 0 ]]
    instance_inter_class = X_train3.iloc[[ 0 ]]
    
    for i, distance in enumerate(dist_matrix[random_number]): # seleccionar la fila respectiva en la matriz de distancias
    
        if ( y_train3.iloc[[  i ]].values[0] == random_sample_category): # distancia intra class 
            if (distance <  distances[0]):
                if (i == random_number):
                    continue
                distances[0] = distance
                instance_intra_class =  X_train3.iloc[[ i ]].copy()
        
        else: # distancia inter class 
            if (distance < distances[1]):
                if (i == random_number):
                    continue
                distances[1] = distance
                instance_inter_class = X_train3.iloc[[ i ]].copy()

    #print("(min distance intra class, min distance inter class): ", (distances[0], distances[1]))

    update_weigh(random_sample, instance_intra_class, instance_inter_class, feature_weighs3, distances, m)


#print("feature_weighs: ")
#print(feature_weighs)

k = int(X_train3.shape[1]*0.3)
#k = 5

idx = np.argpartition(feature_weighs3, -k)[-k:]
indices = idx[np.argsort((-feature_weighs3)[idx])]

#print("indices: ", indices)

#print()
print("top features obesidad: ")

top_features3 = []
for i in indices:
    top_features3.append(obesidad[i])
    print(obesidad[i])

# en el top se encuentra e (excentricidad) y per (perihelio).  Ambos correlacionados. 

top features obesidad: 
gi|537980865|ref|NZ_ACII02000002.1|:c47415-46975
gi|552895565|ref|NZ_AXMI01000001.1|:c282323-281691
gi|483995610|ref|NZ_KB893669.1|:c8033-7407
gi|483995237|ref|NZ_KB893625.1|:466398-466718
gi|134301158|ref|NZ_AAVM02000001.1|:c864489-864256
gi|224515453|ref|NZ_GG657759.1|:19802-20305
gi|134301158|ref|NZ_AAVM02000001.1|:859884-860120
gi|329971589|ref|NZ_GL882691.1|:81296-81454
gi|134301158|ref|NZ_AAVM02000001.1|:863184-863756
gi|550275399|ref|NZ_KI440811.1|:c160122-160024
gi|333374444|ref|NZ_GL892032.1|:3083946-3084464
gi|134301158|ref|NZ_AAVM02000001.1|:863777-864259
gi|282882150|ref|NZ_ADDO01000023.1|:35794-36510
gi|300728038|ref|NZ_ADWO01000081.1|:81008-81700
gi|355708280|ref|NZ_JH376568.1|:c185858-185226
gi|410731267|ref|NC_019386.1|:286512-287822
gi|484008871|ref|NZ_KB894669.1|:c8715-7393
gi|485071027|ref|NZ_KB905729.1|:c66486-65971
gi|116871422|ref|NC_008555.1|:c1577718-1577254
k__Bacteria|p__Firmicutes|c__Clostridia|o__Clostridiales|f__Oscillospiraceae|g__O

gi|389575461|ref|NZ_CM001487.1|:c883206-882604
gi|298483313|ref|NZ_GG774817.1|:74945-75787
gi|403976923|ref|NZ_CAEG01000012.1|:c283676-281910
gi|484029948|ref|NZ_HE978647.1|:c781626-780643
gi|545421869|ref|NZ_KE993626.1|:c6501-6370
gi|485091779|ref|NZ_KB907535.1|:18385-18888
gi|423286106|ref|NZ_JH724226.1|:244162-245226
gi|484064236|ref|NZ_CAPH01000013.1|:c441029-440669
gi|303258037|ref|NZ_GL384001.1|:c129113-128832
gi|402306404|ref|NZ_ALJQ01000011.1|:c49099-46181
gi|134301160|ref|NZ_AAVM02000003.1|:72992-73141
gi|546142252|ref|NZ_HE578930.1|:2426-2794
gi|319430459|ref|NZ_GL622553.1|:26519-26746
gi|320099631|ref|NZ_GL636543.1|:c29376-28531
gi|479140210|ref|NC_021010.1|:c1085089-1084655
gi|427412401|ref|NZ_JH992936.1|:741138-742097
gi|336407414|ref|NZ_GL945091.1|:480994-482547
gi|238915976|ref|NC_012778.1|:650105-650989
gi|422350030|ref|NZ_JH815519.1|:c67029-66934
gi|149173026|ref|NZ_ABBX01000120.1|:465-1292
gi|545046238|ref|NZ_AVMC01000051.1|:86320-87066
gi|423346036|ref|NZ_JH976453.1|

gi|479146200|ref|NC_021012.1|:4145365-4145640
gi|224021129|ref|NZ_DS499579.1|:247765-247932
gi|545391856|ref|NZ_KE992501.1|:42871-43599
gi|484006780|ref|NZ_KB894555.1|:34861-35757
gi|378760293|ref|NZ_AGDG01000015.1|:c74597-73683
gi|423340855|ref|NZ_JH976465.1|:316853-317170
gi|253584457|ref|NZ_GG694018.1|:c95944-95450
gi|134301160|ref|NZ_AAVM02000003.1|:c411935-410943
gi|423220654|ref|NZ_JH724081.1|:c19060-17570
gi|483871280|ref|NZ_KB890331.1|:176455-177150
gi|483869302|ref|NZ_KB890322.1|:21428-21898
gi|262405036|ref|NZ_GG705173.1|:1191127-1192152
gi|551720661|ref|NZ_KI391949.1|:92363-92626
gi|163816877|ref|NZ_AAXA02000016.1|:c21830-21609
gi|163816864|ref|NZ_AAXA02000003.1|:17358-17741
gi|345651602|ref|NZ_JH114323.1|:280015-281127
gi|218292481|ref|NZ_ACCK01000066.1|:7466-8350
gi|223667802|ref|NZ_DS480313.1|:6792-7694
gi|224021127|ref|NZ_DS499577.1|:c487274-487107
gi|224021127|ref|NZ_DS499577.1|:c282205-281795
gi|257789778|ref|NC_013204.1|:c1107093-1106359
gi|422327068|ref|NZ_JH590969.1

gi|332522132|ref|NZ_AEUU02000001.1|:1786261-1787097
gi|365822730|ref|NZ_BACR01000011.1|:c40787-40224
gi|512536257|ref|NZ_KE150442.1|:c132464-130317
gi|389842920|ref|NC_017934.1|:c1236834-1235968
gi|423348806|ref|NZ_JH719939.1|:1120489-1121502
gi|545329344|ref|NZ_KE951479.1|:c802-1
gi|365822755|ref|NZ_BACR01000036.1|:6433-6990
gi|312899163|ref|NZ_GL538185.1|:c72253-71450
gi|514340189|ref|NZ_KE148312.1|:c424812-424474
gi|421491232|ref|NZ_ALJO01000012.1|:68344-68928
gi|471331658|ref|NC_020510.1|:97226-98920
gi|545329743|ref|NZ_KE951485.1|:c44370-42493
gi|312899186|ref|NZ_GL538208.1|:250428-250979
gi|224485632|ref|NZ_EQ973486.1|:110048-110252
gi|320099632|ref|NZ_GL636544.1|:28303-29475
gi|479199283|ref|NC_021039.1|:c867446-866820
gi|479199283|ref|NC_021039.1|:2555186-2556658
gi|479199283|ref|NC_021039.1|:456541-457146
gi|479199283|ref|NC_021039.1|:595132-596772
gi|545613167|ref|NZ_KI271072.1|:60507-60641
gi|224485488|ref|NZ_EQ973223.1|:c33200-32601
gi|405322024|ref|NZ_JH815204.1|:790431-79

gi|405322164|ref|NZ_JH815205.1|:327488-328363
gi|405322024|ref|NZ_JH815204.1|:c250697-249426
gi|405321593|ref|NZ_JH815203.1|:947027-947710
gi|405321593|ref|NZ_JH815203.1|:793839-795203
gi|545636341|ref|NZ_KI271540.1|:21786-22031
gi|294806528|ref|NZ_ADKP01000042.1|:c46018-44840
gi|319430552|ref|NZ_GL622506.1|:259709-260530
gi|330998632|ref|NZ_GL883867.1|:c71992-71765
gi|479208076|ref|NC_021042.1|:c655795-655307
gi|482747372|ref|NZ_HE998567.1|:c303761-303306
gi|224485636|ref|NZ_EQ973490.1|:c1055749-1054871
gi|134301160|ref|NZ_AAVM02000003.1|:c379258-376403
gi|303237029|ref|NZ_AEDO01000046.1|:c149748-148903
gi|319430530|ref|NZ_GL622433.1|:c12247-11342
gi|405322164|ref|NZ_JH815205.1|:709831-711000
gi|238922432|ref|NC_012781.1|:c2915688-2915551
gi|373108119|ref|NZ_JH590861.1|:537573-537710
gi|325830025|ref|NZ_AEXR01000008.1|:6286-6432
gi|355632463|ref|NZ_JH376517.1|:c274371-273415
gi|223956307|ref|NZ_DS995509.1|:607490-608872
gi|336434653|ref|NZ_GL945334.1|:c369098-368685
gi|417973729|ref|N

...

gi|307069503|ref|NC_014497.1|:c101352-100888
gi|512436202|ref|NZ_KE159490.1|:c57303-54841
gi|545627717|ref|NZ_KI271528.1|:6807-7151
gi|294644583|ref|NZ_ADMP01000088.1|:c62173-62030
gi|545412122|ref|NZ_KE993339.1|:c6576-6454
gi|448879149|ref|NZ_KB373316.1|:358296-359573
gi|365833710|ref|NZ_JH470429.1|:c29289-28192
gi|254692781|ref|NZ_GG697159.2|:c15842-15066
gi|488641720|ref|NZ_KB851183.1|:1929205-1929744
gi|224515380|ref|NZ_EQ973344.1|:c1306506-1306315
gi|172085036|ref|NZ_ABJL02000008.1|:c2273572-2271983
gi|254692771|ref|NZ_GG697149.2|:c384150-384031
gi|545430709|ref|NZ_KI259364.1|:c6494-5910
gi|116617174|ref|NC_008531.1|:279934-280329
gi|545349709|ref|NZ_KE952243.1|:291-1157
gi|479152295|ref|NC_021014.1|:1689628-1690221
gi|324035747|ref|NZ_GL834306.1|:c329262-328429
gi|237642869|ref|NZ_GG667766.1|:8965-9744
gi|488676649|ref|NZ_KB850952.1|:340048-340929
gi|365845802|ref|NZ_JH417653.1|:c7999-6491
gi|514340170|ref|NZ_KE150405.1|:c3661156-3660374
gi|514340170|ref|NZ_KE150405.1|:c2344510-2

gi|482881633|ref|NC_021081.1|:507978-508364
gi|224485479|ref|NZ_EQ973214.1|:105260-105865
gi|551720627|ref|NZ_KI391947.1|:81013-81471
gi|488661264|ref|NZ_KB851045.1|:1445292-1446764
gi|237642743|ref|NZ_GG667640.1|:7915-9741
gi|479140210|ref|NC_021010.1|:3070406-3070741
gi|224485393|ref|NZ_EQ973128.1|:c358167-358048
gi|562751855|ref|NZ_CM002287.1|:c2058941-2058609
gi|564716896|gb|AZJE01000034.1|:499-1011
gi|355634532|ref|NZ_JH376522.1|:c139641-139063
gi|479146200|ref|NC_021012.1|:3998896-3999078
gi|211596884|ref|NZ_DS264338.1|:c398692-398225
gi|241911872|ref|NZ_ACCL02000037.1|:c19851-19468
gi|484006757|ref|NZ_KB894553.1|:c51095-50769
gi|479185170|ref|NC_021030.1|:c127177-126305
gi|345651597|ref|NZ_JH114350.1|:c368566-367505
gi|224485479|ref|NZ_EQ973214.1|:109379-110269
gi|365845886|ref|NZ_JH417737.1|:289-2793
gi|217076133|ref|NC_011653.1|:1236466-1237131
gi|293374460|ref|NZ_ADMN01000016.1|:c45645-45043
gi|544231849|gb|AWVI01000052.1|:c39180-38188
gi|488663589|ref|NZ_KB851048.1|:c396532-

gi|422349026|ref|NZ_JH815515.1|:110216-110446
gi|223667733|ref|NZ_DS264553.1|:1266-1976
gi|223667762|ref|NZ_DS264582.1|:c5833-4379
gi|223667762|ref|NZ_DS264582.1|:c8838-7990
gi|334364845|ref|NZ_AENZ01000025.1|:c51770-49815
gi|237642784|ref|NZ_GG667681.1|:c15114-12691
gi|397319973|ref|NZ_JH724315.1|:198929-200371
gi|507077214|ref|NZ_KB976103.1|:c272552-272376
gi|324035747|ref|NZ_GL834306.1|:c474223-473681
gi|324035746|ref|NZ_GL834305.1|:c726272-725127
gi|373471612|ref|NZ_JH591165.1|:c31442-30798
gi|374337044|ref|NC_016749.1|:977824-979419
gi|420155599|ref|NZ_AKFU01000017.1|:57183-58553
gi|479176048|ref|NC_021022.1|:1259255-1260166
gi|405322164|ref|NZ_JH815205.1|:c131898-131149
gi|257789778|ref|NC_013204.1|:c1963111-1962539
gi|444381607|ref|NZ_KB291594.1|:c24239-23622
gi|550889302|ref|NC_022567.1|:c2485904-2485221
gi|479185170|ref|NC_021030.1|:1927631-1928158
gi|269797069|ref|NC_013520.1|:c471436-471065
gi|485041150|ref|NZ_AEMC01000013.1|:43225-43929
gi|294792904|ref|NZ_GG770217.1|:c3361

gi|449961099|ref|NZ_AHRQ01000087.1|:c9420-9175
gi|387774138|ref|NZ_AJSW01000061.1|:c3719-3039
gi|545330260|ref|NZ_KE951492.1|:c42725-42111
gi|450062556|ref|NZ_AHSI01000024.1|:c10464-8803
gi|450123108|ref|NZ_AHST01000059.1|:9190-9336
gi|450148529|ref|NZ_AHSY01000016.1|:c14753-13635
gi|409101469|ref|NC_018867.1|:c1444514-1443303
gi|283767235|ref|NZ_GG730309.1|:c101278-100763
gi|482850134|ref|NZ_AKCI01000001.1|:c285959-285471
gi|422323853|ref|NZ_JH370351.1|:c253934-253674
gi|378773696|ref|NC_016808.1|:1860628-1860846
gi|410463696|ref|NZ_ALAO01000131.1|:c3748-3407
gi|386389849|ref|NZ_AJMU01000062.1|:4671-5240
gi|386388739|ref|NZ_AJMU01000010.1|:29131-29481
gi|320528842|ref|NZ_GL637662.1|:37729-37857
gi|545327623|ref|NZ_KE951414.1|:10903-11538
gi|424661815|ref|NZ_JH815524.1|:1559889-1560200
gi|320535139|ref|NZ_GL637933.1|:5899-6030
gi|405984431|ref|NZ_JH815198.1|:c111189-110698
gi|405984431|ref|NZ_JH815198.1|:552326-553114
gi|66820706|ref|XM_638839.1|
gi|374683956|ref|NZ_GL995195.1|:141673-

gi|84488831|ref|NC_007681.1|:1582342-1583529
gi|84488831|ref|NC_007681.1|:c1245572-1245021
gi|84488831|ref|NC_007681.1|:c625050-624568
gi|238922432|ref|NC_012781.1|:694525-695178
gi|520966415|ref|NZ_ATDL01000016.1|:242611-242880
gi|330998577|ref|NZ_GL883812.1|:98020-99549
gi|313900393|ref|NZ_AENW01000053.1|:c23729-21672
gi|298103479|ref|NZ_GG753639.1|:c506887-506504
gi|488675690|ref|NZ_KB850951.1|:1823325-1823660
gi|488676649|ref|NZ_KB850952.1|:895506-895724
gi|427384149|ref|NZ_JH992941.1|:485095-486102
gi|325579880|ref|NZ_GL872339.1|:c244387-244013
gi|373453948|ref|NZ_JH594448.1|:2412-3128
gi|373453948|ref|NZ_JH594448.1|:5478-5711
gi|422325652|ref|NZ_JH590968.1|:c1297888-1297493
gi|307243662|ref|NZ_ADGQ01000035.1|:74181-74672
gi|335047812|ref|NZ_AFII01000002.1|:c235930-235394
gi|313898566|ref|NZ_AENW01000011.1|:c57725-57555
gi|407681354|ref|NC_018676.1|:c71659-71441
gi|324035756|ref|NZ_GL834315.1|:39630-39950
gi|482850058|ref|NZ_AKCD01000001.1|:1312442-1312666
gi|487647851|ref|NZ_AQTP

## Filtrado

In [158]:
X_train_c = X_train[top_features1]
X_test_c = X_test[top_features1]

In [159]:
X_train_d = X_train2[top_features2]
X_test_d = X_test2[top_features2]

In [160]:
X_train_o = X_train3[top_features3]
X_test_o = X_test3[top_features3]

## Aplicacion: Logistic Regression

### 1.- Cirrosis

In [161]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score

regressor1 = LogisticRegression()
regressor1.fit(X_train_c, y_train)
y_pred_1 = regressor1.predict(X_test_c)
roc1 = roc_auc_score(y_test, y_pred_1)

0.9166666666666666

### 2.- Diabetes

In [162]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score

regressor2 = LogisticRegression()
regressor2.fit(X_train_d, y_train2)
y_pred_2 = regressor2.predict(X_test_d)
roc2 = roc_auc_score(y_test2, y_pred_2)

0.7053973013493253

### 3.- Obesidad

In [163]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score
X
regressor3 = LogisticRegression()
regressor3.fit(X_train_o, y_train3)
y_pred_3 = regressor3.predict(X_test_o)
roc3 = roc_auc_score(y_test3, y_pred_3)

0.6285714285714286

In [ ]:
print('Cirrosis',roc1)
print('Diabetes',roc2)
print('Obesidad',roc3,'\n\n')
print('MUAC',(roc1+roc2+roc3)/3)


# TEST

In [180]:
data_test_abundance['Paciente'] = list(range(data_test_abundance.shape[0]))
data_test_marker['Paciente'] = list(range(data_test_abundance.shape[0]))
data_test_marker.drop(['country','code_study'],axis=1,inplace=True)
data_test_abundance.drop(['gender','country','code_study'],axis=1,inplace=True)

In [225]:
todo = pd.merge(data_test_abundance, data_test_marker, on=["Paciente"])

In [226]:
todo.head()

k__Archaea|p__Euryarchaeota|c__Methanobacteria|o__Methanobacteriales|f__Methanobacteriaceae|g__Methanobrevibacter|s__Methanobrevibacter_smithii  \
0                                            0.00000                                                                                                 
1                                            0.00000                                                                                                 
2                                            0.00986                                                                                                 
3                                            0.00000                                                                                                 
4                                            0.00000                                                                                                 

   k__Archaea|p__Euryarchaeota|c__Methanobacteria|o__Methanobacteriales|f__Methanobacteriaceae|g__Methanobrevibacter|s__Methanobrevibacter_unclassified  \
0                                            0.00000                                                                                                      
1                                            0.00000                                                                                                      
2                                            0.00212                                                                                                      
3                                            0.00000                                                                                                      
4                                            0.00000                                                                                                      

   k__Archaea|p__Euryarchaeota|c__Methanobacteria|o__Methanobacteriales|f__Methanobacteriaceae|g__Methanosphaera|s__Methanosphaera_stadtmanae  \
0                                                0.0                                                                                            
1                                                0.0                                                                                            
2                                                0.0                                                                                            
3                                                0.0                                                                                            
4                                                0.0                                                                                            

   k__Archaea|p__Euryarchaeota|c__Methanococci|o__Methanococcales|f__Methanocaldococcaceae|g__Methanocaldococcaceae_unclassified  \
0                                                0.0                                                                               
1                                                0.0                                                                               
2                                                0.0                                                                               
3                                                0.0                                                                               
4                                                0.0                                                                               

   k__Bacteria|p__Acidobacteria|c__Acidobacteriia|o__Acidobacteriales|f__Acidobacteriaceae|g__Granulicella|s__Granulicella_unclassified  \
0                                                0.0                                                                                      
1                                                0.0                                                                                      
2                                                0.0                                      

In [235]:
scaler_test = StandardScaler()

non_categorical_asteriod=todo.columns
scaler_test.fit(todo)

X_test = pd.DataFrame(scaler_test.transform(todo),columns=non_categorical_asteriod)

In [236]:
todo1 = todo[top_features1]
todo2 = todo[top_features2]
todo3 = todo[top_features3]

In [237]:
todo1=todo1.fillna(0)
todo2=todo2.fillna(0)
todo3=todo3.fillna(0)

In [241]:
nameSample = "sample_submission.csv"
df_sample = pd.read_csv(nameSample)

In [242]:
y_test_c=regressor1.predict(todo1)
y_test_d=regressor2.predict(todo2)
y_test_o=regressor3.predict(todo3)
df_sample['Cirrhosis']=y_test_c
df_sample['Obesity']=y_test_o
df_sample['Diabetes']=y_test_d
df_sample.to_csv("jose_miguel.csv",index=False)#josemiguel.csv